In [2]:
import numpy as np 
import pandas as pd 
from datetime import date

In [3]:
ratios = [0,0.236, 0.382, 0.5 , 0.618, 0.786,1,1.414,1.618]
fiblevels = np.array(ratios)

In [4]:
def RSI(series, period=14):
    delta = series.diff().dropna()
    ups = delta * 0
    downs = ups.copy()
    ups[delta > 0] = delta[delta > 0]
    downs[delta < 0] = -delta[delta < 0]
    ups[ups.index[period-1]] = np.mean( ups[:period] ) #first value is sum of avg gains
    ups = ups.drop(ups.index[:(period-1)])
    downs[downs.index[period-1]] = np.mean( downs[:period] ) #first value is sum of avg losses
    downs = downs.drop(downs.index[:(period-1)])
    rs = ups.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() / \
         downs.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() 
    return 100 - 100 / (1 + rs)


# calculating Stoch RSI (gives the same values as TradingView)
# https://www.tradingview.com/wiki/Stochastic_RSI_(STOCH_RSI) 
def STRSIA(series, period=14, smoothK=3, smoothD=3):
    # Calculate RSI 
    delta = series.diff().dropna()
    ups = delta * 0
    downs = ups.copy()
    ups[delta > 0] = delta[delta > 0]
    downs[delta < 0] = -delta[delta < 0]
    ups[ups.index[period-1]] = np.mean( ups[:period] ) #first value is sum of avg gains
    ups = ups.drop(ups.index[:(period-1)])
    downs[downs.index[period-1]] = np.mean( downs[:period] ) #first value is sum of avg losses
    downs = downs.drop(downs.index[:(period-1)])
    rs = ups.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() / \
         downs.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() 
    rsi = 100 - 100 / (1 + rs)

    # Calculate StochRSI 
    stochrsi  = (rsi - rsi.rolling(period).min()) / (rsi.rolling(period).max() - rsi.rolling(period).min())
    stochrsi_K = stochrsi.rolling(smoothK).mean()
    stochrsi_D = stochrsi_K.rolling(smoothD).mean()
    return stochrsi, stochrsi_K, stochrsi_D

In [5]:
ratios

[0, 0.236, 0.382, 0.5, 0.618, 0.786, 1, 1.414, 1.618]

In [6]:
ada15 = pd.read_json('BN-main/ALGO_USDT-1h.json')
ada15

0       1       2       3       4            5
0      1561161600000  3.4000  3.4400  2.6210  2.7090  2138741.658
1      1561165200000  2.7010  2.7960  2.5300  2.7150   902015.539
2      1561168800000  2.7150  2.7490  2.6010  2.6720   512599.433
3      1561172400000  2.6750  2.7140  2.5400  2.5540   994259.176
4      1561176000000  2.5430  2.5620  2.4760  2.5030   969104.836
...              ...     ...     ...     ...     ...          ...
18040  1626235200000  0.8302  0.8421  0.8280  0.8412   281296.120
18041  1626238800000  0.8406  0.8444  0.8296  0.8306   349385.230
18042  1626242400000  0.8309  0.8389  0.8242  0.8279   807401.290
18043  1626246000000  0.8275  0.8398  0.8266  0.8364   318106.260
18044  1626249600000  0.8370  0.8409  0.8242  0.8258   554169.090

[18045 rows x 6 columns]

In [7]:
ada15.columns=['date','open','high','low','close','volume']
ada15

date    open    high     low   close       volume
0      1561161600000  3.4000  3.4400  2.6210  2.7090  2138741.658
1      1561165200000  2.7010  2.7960  2.5300  2.7150   902015.539
2      1561168800000  2.7150  2.7490  2.6010  2.6720   512599.433
3      1561172400000  2.6750  2.7140  2.5400  2.5540   994259.176
4      1561176000000  2.5430  2.5620  2.4760  2.5030   969104.836
...              ...     ...     ...     ...     ...          ...
18040  1626235200000  0.8302  0.8421  0.8280  0.8412   281296.120
18041  1626238800000  0.8406  0.8444  0.8296  0.8306   349385.230
18042  1626242400000  0.8309  0.8389  0.8242  0.8279   807401.290
18043  1626246000000  0.8275  0.8398  0.8266  0.8364   318106.260
18044  1626249600000  0.8370  0.8409  0.8242  0.8258   554169.090

[18045 rows x 6 columns]

In [8]:
start = pd.to_datetime('2020-01-01')
ada15.date=pd.to_datetime(ada15['date'],unit='ms')
ada15


date    open    high     low   close       volume
0     2019-06-22 00:00:00  3.4000  3.4400  2.6210  2.7090  2138741.658
1     2019-06-22 01:00:00  2.7010  2.7960  2.5300  2.7150   902015.539
2     2019-06-22 02:00:00  2.7150  2.7490  2.6010  2.6720   512599.433
3     2019-06-22 03:00:00  2.6750  2.7140  2.5400  2.5540   994259.176
4     2019-06-22 04:00:00  2.5430  2.5620  2.4760  2.5030   969104.836
...                   ...     ...     ...     ...     ...          ...
18040 2021-07-14 04:00:00  0.8302  0.8421  0.8280  0.8412   281296.120
18041 2021-07-14 05:00:00  0.8406  0.8444  0.8296  0.8306   349385.230
18042 2021-07-14 06:00:00  0.8309  0.8389  0.8242  0.8279   807401.290
18043 2021-07-14 07:00:00  0.8275  0.8398  0.8266  0.8364   318106.260
18044 2021-07-14 08:00:00  0.8370  0.8409  0.8242  0.8258   554169.090

[18045 rows x 6 columns]

In [9]:
start = pd.to_datetime('2021-04-01')
end = pd.to_datetime('2021-05-30')


ada2021 = ada15.loc[(ada15['date']> start)& (ada15['date']< end)].copy()
ada2021['RSI'] = RSI(ada2021['close'])
ada2021['RSI4']=RSI(ada2021['close'],56)
ada2021['RSI8']=RSI(ada2021['close'],112)
ada2021['STRSI'] = STRSIA(ada2021['close'])[0]
ada2021['STRSIK'] = STRSIA(ada2021['close'])[1]
ada2021['STRSID'] = STRSIA(ada2021['close'])[2]

ada2021['STRSI4'] = STRSIA(ada2021['close'],56,12,12)[0]
ada2021['STRSIK4'] = STRSIA(ada2021['close'],56,12,12)[1]
ada2021['STRSID4'] = STRSIA(ada2021['close'],56,12,12)[2]

ada2021['STRSI8'] = STRSIA(ada2021['close'],112,24,24)[0]
ada2021['STRSIK8'] = STRSIA(ada2021['close'],112,24,24)[1]
ada2021['STRSID8'] = STRSIA(ada2021['close'],112,24,24)[2]



ada2021

date    open    high     low   close      volume  \
15546 2021-04-01 01:00:00  1.3592  1.3950  1.3541  1.3833  1507079.16   
15547 2021-04-01 02:00:00  1.3838  1.3969  1.3660  1.3660  1011878.63   
15548 2021-04-01 03:00:00  1.3661  1.3960  1.3536  1.3611  1601270.18   
15549 2021-04-01 04:00:00  1.3611  1.3648  1.3502  1.3624  1425959.97   
15550 2021-04-01 05:00:00  1.3624  1.3700  1.3404  1.3404  1007317.36   
...                   ...     ...     ...     ...     ...         ...   
16951 2021-05-29 19:00:00  0.8134  0.8174  0.7911  0.8079  1071935.29   
16952 2021-05-29 20:00:00  0.8074  0.8167  0.7904  0.8118  1028037.66   
16953 2021-05-29 21:00:00  0.8127  0.8272  0.8099  0.8245   680798.46   
16954 2021-05-29 22:00:00  0.8243  0.8310  0.8122  0.8247   691633.36   
16955 2021-05-29 23:00:00  0.8247  0.8410  0.8100  0.8315   790073.62   

             RSI       RSI4       RSI8     STRSI    STRSIK    STRSID  \
15546        NaN        NaN        NaN       NaN       NaN       NaN   
15547        NaN        NaN        NaN       NaN       NaN       NaN   
15548        NaN        NaN        NaN       NaN       NaN       NaN   
15549        NaN        NaN        NaN       NaN       NaN       NaN   
15550        NaN        NaN        NaN       NaN       NaN       NaN   
...          ...        ...        ...       ...       ...       ...   
16951  31.979970  42.438440  45.096552  0.057512  0.056794  0.100793   
16952  33.544663  42.717779  45.213377  0.187055  0.119146  0.105848   
16953  38.505474  43.624870  45.593758  0.639752  0.294773  0.156905   
16954  38.583228  43.639181  45.599760  0.646443  0.491084  0.301668   
16955  41.300794  44.130150  45.804853  0.880299  0.722165  0.502674   

         STRSI4   STRSIK4   STRSID4    STRSI8   STRSIK8   STRSID8  
15546       NaN       NaN       NaN       NaN       NaN       NaN  
15547       NaN       NaN       NaN       NaN       NaN       NaN  
15548       NaN       NaN       NaN       NaN       NaN       NaN  
15549       NaN       NaN       NaN       NaN       NaN       NaN  
15550       NaN       NaN       NaN       NaN       NaN       NaN  
...         ...       ...       ...       ...       ...       ...  
16951  0.007442  0.120839  0.279140  0.003365  0.204670  0.402638  
16952  0.036372  0.103380  0.256839  0.026377  0.192604  0.385450  
16953  0.132824  0.092657  0.232669  0.101304  0.190176  0.369363  
16954  0.139841  0.085452  0.207713  0.102486  0.187974  0.354313  
16955  0.205146  0.078429  0.182827  0.142885  0.180696  0.339807  

[1410 rows x 18 columns]

In [10]:
#maxlevels = [13,13,13,13,13,13,13]
#maxlevels = np.array(maxlevels)
#maxlevels

In [11]:
#minlevels = [11,11,11,11,11,11,11]
#minlevels = np.array(minlevels)
#minlevels

In [12]:
ada2021

date    open    high     low   close      volume  \
15546 2021-04-01 01:00:00  1.3592  1.3950  1.3541  1.3833  1507079.16   
15547 2021-04-01 02:00:00  1.3838  1.3969  1.3660  1.3660  1011878.63   
15548 2021-04-01 03:00:00  1.3661  1.3960  1.3536  1.3611  1601270.18   
15549 2021-04-01 04:00:00  1.3611  1.3648  1.3502  1.3624  1425959.97   
15550 2021-04-01 05:00:00  1.3624  1.3700  1.3404  1.3404  1007317.36   
...                   ...     ...     ...     ...     ...         ...   
16951 2021-05-29 19:00:00  0.8134  0.8174  0.7911  0.8079  1071935.29   
16952 2021-05-29 20:00:00  0.8074  0.8167  0.7904  0.8118  1028037.66   
16953 2021-05-29 21:00:00  0.8127  0.8272  0.8099  0.8245   680798.46   
16954 2021-05-29 22:00:00  0.8243  0.8310  0.8122  0.8247   691633.36   
16955 2021-05-29 23:00:00  0.8247  0.8410  0.8100  0.8315   790073.62   

             RSI       RSI4       RSI8     STRSI    STRSIK    STRSID  \
15546        NaN        NaN        NaN       NaN       NaN       NaN   
15547        NaN        NaN        NaN       NaN       NaN       NaN   
15548        NaN        NaN        NaN       NaN       NaN       NaN   
15549        NaN        NaN        NaN       NaN       NaN       NaN   
15550        NaN        NaN        NaN       NaN       NaN       NaN   
...          ...        ...        ...       ...       ...       ...   
16951  31.979970  42.438440  45.096552  0.057512  0.056794  0.100793   
16952  33.544663  42.717779  45.213377  0.187055  0.119146  0.105848   
16953  38.505474  43.624870  45.593758  0.639752  0.294773  0.156905   
16954  38.583228  43.639181  45.599760  0.646443  0.491084  0.301668   
16955  41.300794  44.130150  45.804853  0.880299  0.722165  0.502674   

         STRSI4   STRSIK4   STRSID4    STRSI8   STRSIK8   STRSID8  
15546       NaN       NaN       NaN       NaN       NaN       NaN  
15547       NaN       NaN       NaN       NaN       NaN       NaN  
15548       NaN       NaN       NaN       NaN       NaN       NaN  
15549       NaN       NaN       NaN       NaN       NaN       NaN  
15550       NaN       NaN       NaN       NaN       NaN       NaN  
...         ...       ...       ...       ...       ...       ...  
16951  0.007442  0.120839  0.279140  0.003365  0.204670  0.402638  
16952  0.036372  0.103380  0.256839  0.026377  0.192604  0.385450  
16953  0.132824  0.092657  0.232669  0.101304  0.190176  0.369363  
16954  0.139841  0.085452  0.207713  0.102486  0.187974  0.354313  
16955  0.205146  0.078429  0.182827  0.142885  0.180696  0.339807  

[1410 rows x 18 columns]

In [13]:
high = ada2021.high
low = ada2021.low
maximums5 = high.rolling(5,5)
max5 = maximums5.max()
minimums5 = low.rolling(5,5)
min5 = minimums5.min()
maximums10 = high.rolling(10,10)
max10 = maximums10.max()
minimums10 = low.rolling(10,10)
min10 = minimums10.min()


In [14]:
len(max5)

1410

In [15]:

ada2021['max5'] = max5
ada2021['max10'] = max10
ada2021['min5'] = min5
ada2021['min10'] = min10

ada2021.tail()

date    open    high     low   close      volume  \
16951 2021-05-29 19:00:00  0.8134  0.8174  0.7911  0.8079  1071935.29   
16952 2021-05-29 20:00:00  0.8074  0.8167  0.7904  0.8118  1028037.66   
16953 2021-05-29 21:00:00  0.8127  0.8272  0.8099  0.8245   680798.46   
16954 2021-05-29 22:00:00  0.8243  0.8310  0.8122  0.8247   691633.36   
16955 2021-05-29 23:00:00  0.8247  0.8410  0.8100  0.8315   790073.62   

             RSI       RSI4       RSI8     STRSI  ...    STRSI4   STRSIK4  \
16951  31.979970  42.438440  45.096552  0.057512  ...  0.007442  0.120839   
16952  33.544663  42.717779  45.213377  0.187055  ...  0.036372  0.103380   
16953  38.505474  43.624870  45.593758  0.639752  ...  0.132824  0.092657   
16954  38.583228  43.639181  45.599760  0.646443  ...  0.139841  0.085452   
16955  41.300794  44.130150  45.804853  0.880299  ...  0.205146  0.078429   

        STRSID4    STRSI8   STRSIK8   STRSID8    max5   max10    min5   min10  
16951  0.279140  0.003365  0.204670  0.402638  0.8468  0.8811  0.7911  0.7911  
16952  0.256839  0.026377  0.192604  0.385450  0.8468  0.8811  0.7904  0.7904  
16953  0.232669  0.101304  0.190176  0.369363  0.8421  0.8771  0.7904  0.7904  
16954  0.207713  0.102486  0.187974  0.354313  0.8310  0.8571  0.7904  0.7904  
16955  0.182827  0.142885  0.180696  0.339807  0.8410  0.8522  0.7904  0.7904  

[5 rows x 22 columns]

In [16]:
#maxnew = np.ones_like(ratios)
#maxnew

In [17]:
#addmin = mintest.tolist()
#addmax = maxtest.tolist()
#data = pd.DataFrame({"max":maxtest,"min":mintest},dtype='float')
#data = data.append(addmin,ignore_index=True)
#data1 = pd.DataFrame(maxtest)
#data2 = pd.DataFrame(mintest)
#data = pd.DataFrame(data1,data2)

In [18]:
#datamul = data.mul([2,1],axis='columns')
#datamul = data['max'].mul(ratios[7])

In [19]:
#datamul

In [20]:
#df = ada2021.loc[(ada2021['max10']>0)& (ada2021['min10']>0)]
df = ada2021
#len(df['date'])
average = df['max5']-df['min5']
avg = average.mean()
avg
df
#point = df.loc[(df['max5'].diff()>0)]
#pointm = df.loc[(df['min5'].diff()>0)]

df['support5']= df.min5.rolling(5,5).min()
df['support10']= df.min10.rolling(10,10).min()
df['resist5']= df.max5.rolling(5,5).max()
df['resist10']= df.max10.rolling(10,10).max()

#df['RSI'] = RSI(df['close'])
#df['STRSI4']=STRSIA(df['close'],56,12,12)
#df['STRSI8']=STRSIA(df['close'],112,24,24)


point = df[(df['max5'] > df['max5'].shift(1)) &  (df['max5'].shift(1) > df['max5'].shift(2))]
pointm = df[(df['min5'] < df['min5'].shift(1)) &  (df['min5'].shift(1) > df['min5'].shift(2))]
point
#ada2021
pointm

#for row in range(0,len(pointm)):
#    print(pointm['support5'])

date    open    high     low   close      volume  \
15569 2021-04-02 00:00:00  1.3219  1.3277  1.3027  1.3068  1125554.19   
15582 2021-04-02 13:00:00  1.3413  1.3431  1.3136  1.3315  1473098.15   
15588 2021-04-02 19:00:00  1.3382  1.3488  1.3187  1.3423  1664655.44   
15609 2021-04-03 16:00:00  1.4018  1.4239  1.3726  1.3840  4766729.71   
15629 2021-04-04 12:00:00  1.3058  1.3300  1.2889  1.3268  1846727.70   
...                   ...     ...     ...     ...     ...         ...   
16783 2021-05-22 19:00:00  0.9699  0.9900  0.9512  0.9534  1160581.92   
16794 2021-05-23 06:00:00  0.9942  1.0050  0.9561  0.9682  1346650.90   
16846 2021-05-25 10:00:00  0.9291  0.9298  0.8714  0.8927  2233040.26   
16857 2021-05-25 21:00:00  0.9494  0.9571  0.9333  0.9510  1574610.07   
16900 2021-05-27 16:00:00  1.0101  1.0159  0.9868  0.9927  1094203.33   

             RSI       RSI4       RSI8     STRSI  ...   STRSIK8   STRSID8  \
15569  33.324316        NaN        NaN       NaN  ...       NaN       NaN   
15582  46.402983        NaN        NaN  0.547114  ...       NaN       NaN   
15588  50.666156        NaN        NaN  0.595092  ...       NaN       NaN   
15609  49.516662  49.700793        NaN  0.000000  ...       NaN       NaN   
15629  49.901000  47.465820        NaN  0.928827  ...       NaN       NaN   
...          ...        ...        ...       ...  ...       ...       ...   
16783  45.527475  44.370210  44.963931  0.482268  ...  0.515100  0.527343   
16794  45.704447  45.499153  45.567293  0.014261  ...  0.608183  0.530059   
16846  41.350883  46.640973  46.205417  0.000000  ...  0.913129  0.794745   
16857  51.754602  49.375680  47.665855  0.686708  ...  0.875630  0.884583   
16900  48.711068  50.504887  48.849661  0.497424  ...  0.853799  0.891368   

         max5   max10    min5   min10  support5  support10  resist5  resist10  
15569  1.3416  1.3556  1.3027  1.2916    1.2916     1.2916   1.3556    1.4000  
15582  1.3692  1.3692  1.3136  1.3087    1.3103     1.3026   1.3692    1.3692  
15588  1.3519  1.3692  1.3187  1.3136    1.3136     1.3026   1.3692    1.3692  
15609  1.4700  1.4700  1.3726  1.3647    1.3647     1.3279   1.4700    1.4700  
15629  1.3355  1.3355  1.2889  1.2798    1.2798     1.2327   1.3355    1.3577  
...       ...     ...     ...     ...       ...        ...      ...       ...  
16783  1.0153  1.0153  0.9512  0.9174    0.9422     0.8552   1.0153    1.0153  
16794  1.0219  1.0405  0.9561  0.9561    0.9561     0.9422   1.0405    1.0405  
16846  0.9799  1.0088  0.8714  0.8714    0.8714     0.8714   0.9799    1.0179  
16857  0.9881  0.9895  0.9333  0.8672    0.8911     0.8672   0.9895    0.9895  
16900  1.0333  1.0333  0.9868  0.9651    0.9651     0.9356   1.0333    1.0333  

[68 rows x 26 columns]

In [21]:
buypoints = df[(df['STRSI'] < 0.1) &  (df['STRSI4'] < 0.1) & (df['STRSI8'] < 0.1) & (df['close'] <  df['support10'].shift(1)) & (df['RSI']<30)]
sellpoints = df[(df['STRSI'] == 1) &  (df['STRSI4'] == 1) & (df['STRSI8'] == 1) & (df['RSI']>90)]

#buypoints = df.loc[(df['STRSI'] == 0) &  (df['STRSI4'] == 0) & (df['STRSI8'] == 0)]
buypoints
#sellpoints

date    open    high     low   close       volume  \
15956 2021-04-18 03:00:00  1.5632  1.5854  1.2116  1.4004  10981447.99   
15993 2021-04-19 16:00:00  1.3257  1.3719  1.2953  1.3005   6803268.20   
16001 2021-04-20 00:00:00  1.2916  1.3014  1.1600  1.1978   6940064.65   
16072 2021-04-23 01:00:00  1.1605  1.1764  1.0531  1.0894   7906425.22   
16073 2021-04-23 02:00:00  1.0854  1.1070  0.9130  1.0479  11643077.57   
16495 2021-05-10 19:00:00  1.4406  1.4457  1.3637  1.3801   3336995.23   
16547 2021-05-12 23:00:00  1.3789  1.3812  1.2396  1.2734   3714408.04   
16696 2021-05-19 04:00:00  1.2747  1.2868  1.1488  1.1825   5528691.64   
16703 2021-05-19 11:00:00  1.1582  1.1628  1.0200  1.0820   7616166.23   
16704 2021-05-19 12:00:00  1.0821  1.0949  0.7850  0.8740   9602292.24   

             RSI       RSI4       RSI8  STRSI  ...   STRSIK8   STRSID8  \
15956  28.172434  44.353405  47.709160    0.0  ...  0.713726  0.600703   
15993  29.321156  43.003013  46.211611    0.0  ...  0.312603  0.300905   
16001  26.660890  40.580276  44.510345    0.0  ...  0.235794  0.290912   
16072  26.480044  41.216905  44.327765    0.0  ...  0.247343  0.213552   
16073  23.266798  39.929012  43.599034    0.0  ...  0.240551  0.216154   
16495  27.602487  43.302875  47.623593    0.0  ...  0.146343  0.238869   
16547  24.327563  40.380193  45.173505    0.0  ...  0.270929  0.283621   
16696  27.103626  41.773990  45.079937    0.0  ...  0.344643  0.319096   
16703  22.947406  38.720606  43.182930    0.0  ...  0.234327  0.315748   
16704  14.152048  32.890607  39.433435    0.0  ...  0.219127  0.312994   

         max5   max10    min5   min10  support5  support10  resist5  resist10  
15956  1.7190  1.7999  1.2116  1.2116    1.2116     1.2116   1.7999    1.7999  
15993  1.4889  1.5095  1.2953  1.2953    1.2953     1.2953   1.5095    1.5300  
16001  1.3650  1.3800  1.1600  1.1600    1.1600     1.1600   1.3800    1.5095  
16072  1.2117  1.3197  1.0531  1.0531    1.0531     1.0531   1.3127    1.3251  
16073  1.2117  1.3127  0.9130  0.9130    0.9130     0.9130   1.2677    1.3251  
16495  1.4926  1.5035  1.3637  1.3637    1.3637     1.3637   1.4937    1.5561  
16547  1.4166  1.4460  1.2396  1.2396    1.2396     1.2396   1.4307    1.4898  
16696  1.3880  1.3880  1.1488  1.1488    1.1488     1.1488   1.3880    1.3930  
16703  1.2140  1.3126  1.0200  1.0200    1.0200     1.0200   1.2886    1.3880  
16704  1.2140  1.2886  0.7850  0.7850    0.7850     0.7850   1.2868    1.3880  

[10 rows x 26 columns]

In [22]:
import plotly.graph_objs as go
from plotly.subplots import make_subplots
import plotly.express as px



#Declare figure


fig = go.Figure()

fig = make_subplots(rows=8, cols=1,subplot_titles=("Price","gap","empty", "RSI 1 4 8", "Stoch 1", "Stoch 4","Stoch 8","Stoch 1 4 8"))
    

    
# buy points     
fig.add_trace(
    go.Scatter(x=buypoints.date, y=buypoints['close'],name="buy", mode = "markers+text"), row=1, col=1 
)    

# sell points     
fig.add_trace(
    go.Scatter(x=sellpoints.date, y=sellpoints['close'],name="sell", mode = "markers"), row=1, col=1 
) 
    
# buy points     
fig.add_trace(
    go.Scatter(x=buypoints.date, y=buypoints['resist10'],
        name="resist10",
        text="resist10",
        textposition="top center"),
    row=1, col=1
)  
# resistance 10 


fig.add_trace(
    go.Scatter(x=df.date, y=df['RSI'],
        name="RSI",
        text="RSI",
        textposition="top center"),
    row=4, col=1
)

# support 10
fig.add_trace(
    go.Scatter(x=buypoints.date, y=buypoints['support10'],
        name="support10",
        text="support1010",
        textposition="top center"),
    row=1, col=1
)  

fig.add_trace(
    go.Scatter(x=df.date, y=df['RSI4'],name="RSI4"),
    row=4, col=1
)

fig.add_trace(
    go.Scatter(x=df.date, y=df['RSI8'],name="RSI8"),
    row=4, col=1
)

fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI'],name="STRSI"),
    row=5, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSIK'],name="STRSIK"),
    row=5, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSID'],name="STRSID"),
    row=5, col=1
)
    
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI4'],name="STRSI4"),
    row=6, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSIK4'],name="STRSIK4"),
    row=6, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSID4'],name="STRSID4"),
    row=6, col=1
)
    
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI8'],name="STRSI8"),
    row=7, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSIK8'],name="STRSIK8"),
    row=7, col=1
)

fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSID8'],name="STRSIK8"),
    row=7, col=1
)


fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI8'],name="STRSI8"),
    row=8, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI4'],name="STRSI4"),
    row=8, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI'],name="STRSI"),
    row=8, col=1
)


#add Traces

fig.add_trace(go.Candlestick(x=df.date,
                open=df['open'],
                high=df['high'],
                low=df['low'],
                close=df['close'], name = 'market data'),row=1,col=1)

#fig.add_trace(go.Scatter(x=df['date'], y=df['max10']))

#fig.add_trace(go.Scatter(x=df['date'], y=df['min10']))

#fig.add_trace(go.Scatter(x=point['date'], y=point['resist5']))

#fig.add_trace(go.Scatter(x=pointm['date'], y=pointm['support5']))


#fig.add_shape(type="line",
#    x0=pointm['date'], y0=pointm['support5'], x1=max(pointm['date']), y1=pointm['support5'],
#    line=dict(
#        color="LightSeaGreen",
#        width=4,
#        dash="dashdot",
#    ))
fig.update_shapes(dict(xref='x', yref='y'))

#for index in range(0,len(pointm)):
    #fig.add_hline(y=pointm['support5'])

#fig.add_trace(go.Scatter(x=point['date'], y=point['resist10']))

#fig.add_trace(go.Scatter(x=pointm['date'], y=pointm['support10']))
#for i in range(len(df['date'])):
    #fig.add_hline(y=df[i]['min10'], line_dash="dot",
                  #annotation_text="support", 
                  #annotation_position="bottom right")

#fig.add_hline(y=df['max10'], line_dash="dot",
#              annotation_text="resitance", 
#              annotation_position="bottom right")



fig.update_layout(height=3000, width=800, title_text="top sub plots")
# X and Y Axis Update
fig.update_xaxes(
    title = 'Date',rangeslider_visible=False
)

#fig.update_yaxes(
#    title = 'Share Price (USD)'
#)

#Show
fig.show()

In [22]:
import plotly.graph_objs as go

import plotly.express as px
import pandas as pd


px.scatter(x=buypoints.date, y=buypoints['close'])



fig.show()